
### Data Warehousing Final Project


For this project, I analyzed a dataset that originally had a total of 172,000 rows of ticket sales transactions from various events during Winter Fest OC, a festival held in Orange County, California, meant to celebrate the magic of winter.

I organized my data through a medallion lakehouse architecture of bronze, silver, and gold layers, and concluded with an analysis alongside visuals. All dimension and fact tables created throughout this project were stored in AWS S3.

Once fully processed into the gold layer, I created charts and analysis for the following relationships: ticket sales proportions in relation to affiliates, total revenue/ticket sales as they relate to order location, and ticket sales observed over time.


### AWS Mount to S3 Bucket

In [0]:
%fs

ls /mnt/mount

path name size modificationTime dbfs:/mnt/mount/fall_2023_finals/ fall_2023_finals/ 0 0

In [0]:
%fs

ls /mnt/mount/fall_2023_finals/TicketSales

path name size modificationTime dbfs:/mnt/mount/fall_2023_finals/TicketSales/bronze/ bronze/ 0 0 dbfs:/mnt/mount/fall_2023_finals/TicketSales/gold/ gold/ 0 0 dbfs:/mnt/mount/fall_2023_finals/TicketSales/silver/ silver/ 0 0


### Bronze Layer

In [0]:
%py

dbutils.fs.rm("/user/hive/warehouse/fall_2023_finals.db/",True)

Out[4]: True

In [0]:
%sql

drop database if exists fall_2023_finals cascade;

In [0]:
%sql
 
create database if not exists fall_2023_finals;

In [0]:
%sql

use fall_2023_finals

In [0]:
%sql
 
drop table if exists bronze_TicketSales_csv

In [0]:
%sql
create table bronze_TicketSales_csv using csv options(
  path = '/mnt/mount/fall_2023_finals/TicketSales/bronze/raw_data',
  header = 'true',
  inferSchema = 'true',
  delimiter = ','
);

In [0]:
%sql
 
select * from bronze_TicketSales_csv limit 5;

event_id order_id order_date email quantity ticket_type attendee_id buyer_email event_date order_city order_state order_country discount affiliate total_paid home_address_1 home_address_2 home_city home_state home_zip home_country what_are_you_most_excited_for_at_winter_fest_oc how_did_you_hear_about_winter_fest_oc have_you_attended_winter_fest_oc_before did_you_attend_winter_fest_oc_last_year billing_address_1 billing_address_2 billing_city billing_state billing_country billing_zip zip 38878678173 709113897 2017-12-17T00:20:18.000+0000 patty.delpilar.patty.delpilar.roman@gmail.com 1 Online Child General Admission (3 - 12 years old) 885484430 patty.delpilar.patty.delpilar.roman@gmail.com 2017-12-21T17:00:00.000+0000 Santa Ana CA United States null erelpanelorg 15.69 null null null null null null Santa and his reindeer flying over the Fairgrounds through December 24th, before they return to the North Pole | Strolling through the Festival of Lights | Nightly Christmas Tree Lighting Celebration with Parade of Winter Fest OC Characters, Snow Flurries and Fireworks Other Event null null null null null null null null null 38878678173 702831510 2017-11-28T06:12:49.000+0000 classicquilting@gmail.com 1 Groupon: One Single-Day Child General Admission Pass and Snowflake Summit Ice Tubing Fast Pass 877795034 classicquilting@gmail.com 2017-12-21T17:00:00.000+0000 Costa Mesa CA United States RTGYNBHP null 0.0 null null null null null null Santa and his reindeer flying over the Fairgrounds through December 24th, before they return to the North Pole | Intimate Meet & Greet with Santa & Mrs. Claus in their Cabin through Christmas Eve | Ice Skating under the stars on SoCal's largest ice rink Other Event null null null null null null null null null 38878678173 710021007 2017-12-21T00:15:05.000+0000 adv92867@hotmail.com 1 Online Platinum Ice Pass Presented By Orange County SC- Admission + Ice Skating + Unlimited Carnival Rides + Snowflake Summit Ice Tube Fast Pass + Orange County SC Ticket 886589873 mv92867@hotmail.com 2017-12-21T17:00:00.000+0000 Orange CA United States null echckt 42.99 null null null null null null Strolling through the Festival of Lights Instagram null null null null null null null null null 38878678173 709554356 2017-12-19T05:35:07.000+0000 bgutierrez083@yahoo.com 1 Online Opening Hour Admission (5pm-6pm) 886024400 bgutierrez083@yahoo.com 2017-12-21T17:00:00.000+0000 Fontana CA United States null echckt 13.59 null null null null null null Enjoying holiday food and drink specials Family Member or Friend null null null null null null null null null 38878678173 707778153 2017-12-12T06:27:31.000+0000 a*************5@gmail.com 1 Online Child General Admission (3 - 12 years old) 883858138 a*************5@gmail.com 2017-12-21T17:00:00.000+0000 Palmdale CA United States null null 15.69 null null null null null null Santa and his reindeer flying over the Fairgrounds through December 24th, before they return to the North Pole | Ice Tubing down Snowflake Summit in the Ice Hangar | Newly Expanded - Snow Play & Slides with fresh snow blown in daily | Strolling through the Festival of Lights | Nightly Christmas Tree Lighting Celebration with Parade of Winter Fest OC Characters, Snow Flurries and Fireworks | Santa's Toddler Play Area Facebook null null null null null null null null null

In [0]:
%sql
 
show create table bronze_TicketSales_csv

createtab_stmt CREATE TABLE fall_2023_finals.bronze_ticketsales_csv (
 event_id BIGINT,
 order_id INT,
 order_date TIMESTAMP,
 email STRING,
 quantity INT,
 ticket_type STRING,
 attendee_id INT,
 buyer_email STRING,
 event_date TIMESTAMP,
 order_city STRING,
 order_state STRING,
 order_country STRING,
 discount STRING,
 affiliate STRING,
 total_paid DOUBLE,
 home_address_1 STRING,
 home_address_2 STRING,
 home_city STRING,
 home_state STRING,
 home_zip STRING,
 home_country STRING,
 what_are_you_most_excited_for_at_winter_fest_oc STRING,
 how_did_you_hear_about_winter_fest_oc STRING,
 have_you_attended_winter_fest_oc_before STRING,
 did_you_attend_winter_fest_oc_last_year STRING,
 billing_address_1 STRING,
 billing_address_2 STRING,
 billing_city STRING,
 billing_state STRING,
 billing_country STRING,
 billing_zip STRING,
 zip STRING)
USING csv
OPTIONS (
 'delimiter' = ',',
 'header' = 'true',
 'inferSchema' = 'true')
LOCATION 'dbfs:/mnt/mount/fall_2023_finals/TicketSales/bronze/raw_data'

In [0]:
%sql
CREATE TABLE fall_2023_finals.bronze_TcktSales_csv (
  event_id BIGINT,
  order_id INT,
  order_date TIMESTAMP,
  email STRING,
  quantity INT,
  ticket_type STRING,
  attendee_id INT,
  buyer_email STRING,
  event_date TIMESTAMP,
  order_city STRING,
  order_state STRING,
  order_country STRING,
  discount STRING,
  affiliate STRING,
  total_paid DOUBLE,
  home_address_1 STRING,
  home_address_2 STRING,
  home_city STRING,
  home_state STRING,
  home_zip INT,
  home_country STRING,
  what_are_you_most_excited_for_at_winter_fest_oc STRING,
  how_did_you_hear_about_winter_fest_oc STRING,
  have_you_attended_winter_fest_oc_before STRING,
  did_you_attend_winter_fest_oc_last_year STRING,
  billing_address_1 STRING,
  billing_address_2 STRING,
  billing_city STRING,
  billing_state STRING,
  billing_country STRING,
  billing_zip INT,
  zip INT)
USING csv
OPTIONS (
  'delimiter' = ',',
  'header' = 'true',
  'inferSchema' = 'true')
LOCATION 'dbfs:/mnt/mount/fall_2023_finals/TicketSales/bronze/raw_data'

In [0]:
%sql
 
select * from bronze_TcktSales_csv limit 5;

event_id order_id order_date email quantity ticket_type attendee_id buyer_email event_date order_city order_state order_country discount affiliate total_paid home_address_1 home_address_2 home_city home_state home_zip home_country what_are_you_most_excited_for_at_winter_fest_oc how_did_you_hear_about_winter_fest_oc have_you_attended_winter_fest_oc_before did_you_attend_winter_fest_oc_last_year billing_address_1 billing_address_2 billing_city billing_state billing_country billing_zip zip 38878678173 709113897 2017-12-17T00:20:18.000+0000 patty.delpilar.patty.delpilar.roman@gmail.com 1 Online Child General Admission (3 - 12 years old) 885484430 patty.delpilar.patty.delpilar.roman@gmail.com 2017-12-21T17:00:00.000+0000 Santa Ana CA United States null erelpanelorg 15.69 null null null null null null Santa and his reindeer flying over the Fairgrounds through December 24th, before they return to the North Pole | Strolling through the Festival of Lights | Nightly Christmas Tree Lighting Celebration with Parade of Winter Fest OC Characters, Snow Flurries and Fireworks Other Event null null null null null null null null null 38878678173 702831510 2017-11-28T06:12:49.000+0000 classicquilting@gmail.com 1 Groupon: One Single-Day Child General Admission Pass and Snowflake Summit Ice Tubing Fast Pass 877795034 classicquilting@gmail.com 2017-12-21T17:00:00.000+0000 Costa Mesa CA United States RTGYNBHP null 0.0 null null null null null null Santa and his reindeer flying over the Fairgrounds through December 24th, before they return to the North Pole | Intimate Meet & Greet with Santa & Mrs. Claus in their Cabin through Christmas Eve | Ice Skating under the stars on SoCal's largest ice rink Other Event null null null null null null null null null 38878678173 710021007 2017-12-21T00:15:05.000+0000 adv92867@hotmail.com 1 Online Platinum Ice Pass Presented By Orange County SC- Admission + Ice Skating + Unlimited Carnival Rides + Snowflake Summit Ice Tube Fast Pass + Orange County SC Ticket 886589873 mv92867@hotmail.com 2017-12-21T17:00:00.000+0000 Orange CA United States null echckt 42.99 null null null null null null Strolling through the Festival of Lights Instagram null null null null null null null null null 38878678173 709554356 2017-12-19T05:35:07.000+0000 bgutierrez083@yahoo.com 1 Online Opening Hour Admission (5pm-6pm) 886024400 bgutierrez083@yahoo.com 2017-12-21T17:00:00.000+0000 Fontana CA United States null echckt 13.59 null null null null null null Enjoying holiday food and drink specials Family Member or Friend null null null null null null null null null 38878678173 707778153 2017-12-12T06:27:31.000+0000 a*************5@gmail.com 1 Online Child General Admission (3 - 12 years old) 883858138 a*************5@gmail.com 2017-12-21T17:00:00.000+0000 Palmdale CA United States null null 15.69 null null null null null null Santa and his reindeer flying over the Fairgrounds through December 24th, before they return to the North Pole | Ice Tubing down Snowflake Summit in the Ice Hangar | Newly Expanded - Snow Play & Slides with fresh snow blown in daily | Strolling through the Festival of Lights | Nightly Christmas Tree Lighting Celebration with Parade of Winter Fest OC Characters, Snow Flurries and Fireworks | Santa's Toddler Play Area Facebook null null null null null null null null null

In [0]:
%sql

drop table if exists fall_2023_finals.bronze_Tcktsales_delta

In [0]:
%sql
CREATE TABLE fall_2023_finals.bronze_TcktSales_delta (
  event_id BIGINT,
  order_id INT,
  order_date TIMESTAMP,
  email STRING,
  quantity INT,
  ticket_type STRING,
  attendee_id INT,
  buyer_email STRING,
  event_date TIMESTAMP,
  order_city STRING,
  order_state STRING,
  order_country STRING,
  discount STRING,
  affiliate STRING,
  total_paid DOUBLE,
  home_address_1 STRING,
  home_address_2 STRING,
  home_city STRING,
  home_state STRING,
  home_zip INT,
  home_country STRING,
  what_are_you_most_excited_for_at_winter_fest_oc STRING,
  how_did_you_hear_about_winter_fest_oc STRING,
  have_you_attended_winter_fest_oc_before STRING,
  did_you_attend_winter_fest_oc_last_year STRING,
  billing_address_1 STRING,
  billing_address_2 STRING,
  billing_city STRING,
  billing_state STRING,
  billing_country STRING,
  billing_zip INT,
  zip INT)
USING delta
OPTIONS (
  'delimiter' = ',',
  'header' = 'true',
  'inferSchema' = 'true')
LOCATION 'dbfs:/mnt/mount/fall_2023_finals/TicketSales/bronze/delta'

In [0]:
%sql

insert into fall_2023_finals.bronze_TcktSales_delta 
select * from  bronze_TcktSales_csv

num_affected_rows num_inserted_rows 171997 171997


At this point, I noticed that an order_location column would prove beneficial for an order_location dimension. I decided to create one using the CONCAT function in SQL to concatenate the values in the order_city, order_state, and order_country columns into a single column.

In [0]:
%sql
alter table bronze_TcktSales_delta
add column order_location STRING;

update bronze_TcktSales_delta
set order_location = concat(order_city, ', ', order_state, ', ', order_country);

num_affected_rows 171997

In [0]:
%sql
 
select count(*) from bronze_TcktSales_delta

count(1) 171997

In [0]:
%sql
 
select * from bronze_TcktSales_delta limit 5

event_id order_id order_date email quantity ticket_type attendee_id buyer_email event_date order_city order_state order_country discount affiliate total_paid home_address_1 home_address_2 home_city home_state home_zip home_country what_are_you_most_excited_for_at_winter_fest_oc how_did_you_hear_about_winter_fest_oc have_you_attended_winter_fest_oc_before did_you_attend_winter_fest_oc_last_year billing_address_1 billing_address_2 billing_city billing_state billing_country billing_zip zip order_location 38878678173 709113897 2017-12-17T00:20:18.000+0000 patty.delpilar.patty.delpilar.roman@gmail.com 1 Online Child General Admission (3 - 12 years old) 885484430 patty.delpilar.patty.delpilar.roman@gmail.com 2017-12-21T17:00:00.000+0000 Santa Ana CA United States null erelpanelorg 15.69 null null null null null null Santa and his reindeer flying over the Fairgrounds through December 24th, before they return to the North Pole | Strolling through the Festival of Lights | Nightly Christmas Tree Lighting Celebration with Parade of Winter Fest OC Characters, Snow Flurries and Fireworks Other Event null null null null null null null null null Santa Ana, CA, United States 38878678173 702831510 2017-11-28T06:12:49.000+0000 classicquilting@gmail.com 1 Groupon: One Single-Day Child General Admission Pass and Snowflake Summit Ice Tubing Fast Pass 877795034 classicquilting@gmail.com 2017-12-21T17:00:00.000+0000 Costa Mesa CA United States RTGYNBHP null 0.0 null null null null null null Santa and his reindeer flying over the Fairgrounds through December 24th, before they return to the North Pole | Intimate Meet & Greet with Santa & Mrs. Claus in their Cabin through Christmas Eve | Ice Skating under the stars on SoCal's largest ice rink Other Event null null null null null null null null null Costa Mesa, CA, United States 38878678173 710021007 2017-12-21T00:15:05.000+0000 adv92867@hotmail.com 1 Online Platinum Ice Pass Presented By Orange County SC- Admission + Ice Skating + Unlimited Carnival Rides + Snowflake Summit Ice Tube Fast Pass + Orange County SC Ticket 886589873 mv92867@hotmail.com 2017-12-21T17:00:00.000+0000 Orange CA United States null echckt 42.99 null null null null null null Strolling through the Festival of Lights Instagram null null null null null null null null null Orange, CA, United States 38878678173 709554356 2017-12-19T05:35:07.000+0000 bgutierrez083@yahoo.com 1 Online Opening Hour Admission (5pm-6pm) 886024400 bgutierrez083@yahoo.com 2017-12-21T17:00:00.000+0000 Fontana CA United States null echckt 13.59 null null null null null null Enjoying holiday food and drink specials Family Member or Friend null null null null null null null null null Fontana, CA, United States 38878678173 707778153 2017-12-12T06:27:31.000+0000 a*************5@gmail.com 1 Online Child General Admission (3 - 12 years old) 883858138 a*************5@gmail.com 2017-12-21T17:00:00.000+0000 Palmdale CA United States null null 15.69 null null null null null null Santa and his reindeer flying over the Fairgrounds through December 24th, before they return to the North Pole | Ice Tubing down Snowflake Summit in the Ice Hangar | Newly Expanded - Snow Play & Slides with fresh snow blown in daily | Strolling through the Festival of Lights | Nightly Christmas Tree Lighting Celebration with Parade of Winter Fest OC Characters, Snow Flurries and Fireworks | Santa's Toddler Play Area Facebook null null null null null null null null null Palmdale, CA, United States


As seen in the final column, an order_location column now exists thanks to the use of the CONCAT function based on the three columns specified.


### Testing for Zeros/Nulls/Corner Cases


At this stage, I will test for zeros/nulls/corner cases for columns my future keys would be derived from later on for fact and dimension tables. As a result, the columns I will perform the aforementioned tests for in the bronze layer consist of order_date, event_id, order_id, attendee_id, and order_location. If the columns ending in "id" turn out not to be suitable as primary keys when developing the dimensional model, surrogate keys will utilized in their stead. For now, however, I will still clean the previously mentinoed columns with the zeros/nulls/corner cases tests.

For date columns a zero test is not necessary due to them being TIMESTAMPs. For column's ending in "id", the corner cases included a test for leading or trailing spaces along with a length test to see if they were out of the expected range.


### Tests for order_date

In [0]:
%sql

select * from bronze_TcktSales_delta where order_date is null

event_id order_id order_date email quantity ticket_type attendee_id buyer_email event_date order_city order_state order_country discount affiliate total_paid home_address_1 home_address_2 home_city home_state home_zip home_country what_are_you_most_excited_for_at_winter_fest_oc how_did_you_hear_about_winter_fest_oc have_you_attended_winter_fest_oc_before did_you_attend_winter_fest_oc_last_year billing_address_1 billing_address_2 billing_city billing_state billing_country billing_zip zip order_location

In [0]:
%sql

select * from bronze_TcktSales_delta where order_date not between '1000-01-01' AND '9999-12-31'

event_id order_id order_date email quantity ticket_type attendee_id buyer_email event_date order_city order_state order_country discount affiliate total_paid home_address_1 home_address_2 home_city home_state home_zip home_country what_are_you_most_excited_for_at_winter_fest_oc how_did_you_hear_about_winter_fest_oc have_you_attended_winter_fest_oc_before did_you_attend_winter_fest_oc_last_year billing_address_1 billing_address_2 billing_city billing_state billing_country billing_zip zip order_location


### Tests for event_date

In [0]:
%sql

select * from bronze_TcktSales_delta where event_date is null

event_id order_id order_date email quantity ticket_type attendee_id buyer_email event_date order_city order_state order_country discount affiliate total_paid home_address_1 home_address_2 home_city home_state home_zip home_country what_are_you_most_excited_for_at_winter_fest_oc how_did_you_hear_about_winter_fest_oc have_you_attended_winter_fest_oc_before did_you_attend_winter_fest_oc_last_year billing_address_1 billing_address_2 billing_city billing_state billing_country billing_zip zip order_location

In [0]:
%sql

select * from bronze_TcktSales_delta where event_date not between '1000-01-01' AND '9999-12-31'

event_id order_id order_date email quantity ticket_type attendee_id buyer_email event_date order_city order_state order_country discount affiliate total_paid home_address_1 home_address_2 home_city home_state home_zip home_country what_are_you_most_excited_for_at_winter_fest_oc how_did_you_hear_about_winter_fest_oc have_you_attended_winter_fest_oc_before did_you_attend_winter_fest_oc_last_year billing_address_1 billing_address_2 billing_city billing_state billing_country billing_zip zip order_location


### Tests for event_id

In [0]:
%sql

select * from bronze_TcktSales_delta where event_id = 0

event_id order_id order_date email quantity ticket_type attendee_id buyer_email event_date order_city order_state order_country discount affiliate total_paid home_address_1 home_address_2 home_city home_state home_zip home_country what_are_you_most_excited_for_at_winter_fest_oc how_did_you_hear_about_winter_fest_oc have_you_attended_winter_fest_oc_before did_you_attend_winter_fest_oc_last_year billing_address_1 billing_address_2 billing_city billing_state billing_country billing_zip zip order_location

In [0]:
%sql

select * from bronze_TcktSales_delta where event_id is null

event_id order_id order_date email quantity ticket_type attendee_id buyer_email event_date order_city order_state order_country discount affiliate total_paid home_address_1 home_address_2 home_city home_state home_zip home_country what_are_you_most_excited_for_at_winter_fest_oc how_did_you_hear_about_winter_fest_oc have_you_attended_winter_fest_oc_before did_you_attend_winter_fest_oc_last_year billing_address_1 billing_address_2 billing_city billing_state billing_country billing_zip zip order_location

In [0]:
%sql

select * from bronze_TcktSales_delta where event_id like ' %' OR event_id like '% '

event_id order_id order_date email quantity ticket_type attendee_id buyer_email event_date order_city order_state order_country discount affiliate total_paid home_address_1 home_address_2 home_city home_state home_zip home_country what_are_you_most_excited_for_at_winter_fest_oc how_did_you_hear_about_winter_fest_oc have_you_attended_winter_fest_oc_before did_you_attend_winter_fest_oc_last_year billing_address_1 billing_address_2 billing_city billing_state billing_country billing_zip zip order_location

In [0]:
%sql

select * from bronze_TcktSales_delta where length(event_id) > 11

event_id order_id order_date email quantity ticket_type attendee_id buyer_email event_date order_city order_state order_country discount affiliate total_paid home_address_1 home_address_2 home_city home_state home_zip home_country what_are_you_most_excited_for_at_winter_fest_oc how_did_you_hear_about_winter_fest_oc have_you_attended_winter_fest_oc_before did_you_attend_winter_fest_oc_last_year billing_address_1 billing_address_2 billing_city billing_state billing_country billing_zip zip order_location


### Tests for order_id

In [0]:
%sql

select * from bronze_TcktSales_delta where order_id = 0

event_id order_id order_date email quantity ticket_type attendee_id buyer_email event_date order_city order_state order_country discount affiliate total_paid home_address_1 home_address_2 home_city home_state home_zip home_country what_are_you_most_excited_for_at_winter_fest_oc how_did_you_hear_about_winter_fest_oc have_you_attended_winter_fest_oc_before did_you_attend_winter_fest_oc_last_year billing_address_1 billing_address_2 billing_city billing_state billing_country billing_zip zip order_location

In [0]:
%sql

select * from bronze_TcktSales_delta where order_id is null

event_id order_id order_date email quantity ticket_type attendee_id buyer_email event_date order_city order_state order_country discount affiliate total_paid home_address_1 home_address_2 home_city home_state home_zip home_country what_are_you_most_excited_for_at_winter_fest_oc how_did_you_hear_about_winter_fest_oc have_you_attended_winter_fest_oc_before did_you_attend_winter_fest_oc_last_year billing_address_1 billing_address_2 billing_city billing_state billing_country billing_zip zip order_location

In [0]:
%sql

select * from bronze_TcktSales_delta where order_id like ' %' OR order_id like '% '

event_id order_id order_date email quantity ticket_type attendee_id buyer_email event_date order_city order_state order_country discount affiliate total_paid home_address_1 home_address_2 home_city home_state home_zip home_country what_are_you_most_excited_for_at_winter_fest_oc how_did_you_hear_about_winter_fest_oc have_you_attended_winter_fest_oc_before did_you_attend_winter_fest_oc_last_year billing_address_1 billing_address_2 billing_city billing_state billing_country billing_zip zip order_location

In [0]:
%sql

select * from bronze_TcktSales_delta where length(order_id) > 9

event_id order_id order_date email quantity ticket_type attendee_id buyer_email event_date order_city order_state order_country discount affiliate total_paid home_address_1 home_address_2 home_city home_state home_zip home_country what_are_you_most_excited_for_at_winter_fest_oc how_did_you_hear_about_winter_fest_oc have_you_attended_winter_fest_oc_before did_you_attend_winter_fest_oc_last_year billing_address_1 billing_address_2 billing_city billing_state billing_country billing_zip zip order_location


### Tests for order_location

In [0]:
%sql

select * from bronze_TcktSales_delta where order_location = 0

event_id order_id order_date email quantity ticket_type attendee_id buyer_email event_date order_city order_state order_country discount affiliate total_paid home_address_1 home_address_2 home_city home_state home_zip home_country what_are_you_most_excited_for_at_winter_fest_oc how_did_you_hear_about_winter_fest_oc have_you_attended_winter_fest_oc_before did_you_attend_winter_fest_oc_last_year billing_address_1 billing_address_2 billing_city billing_state billing_country billing_zip zip order_location

In [0]:
%sql

select * from bronze_TcktSales_delta where order_location is null

event_id order_id order_date email quantity ticket_type attendee_id buyer_email event_date order_city order_state order_country discount affiliate total_paid home_address_1 home_address_2 home_city home_state home_zip home_country what_are_you_most_excited_for_at_winter_fest_oc how_did_you_hear_about_winter_fest_oc have_you_attended_winter_fest_oc_before did_you_attend_winter_fest_oc_last_year billing_address_1 billing_address_2 billing_city billing_state billing_country billing_zip zip order_location 38878927920 683912412 2017-10-13T22:57:47.000+0000 help@goldstar.com 1 Goldstar Adult General Admission Plus Ice Slide Fast Pass 854871248 help@goldstar.com 2017-12-23T12:00:00.000+0000 United States null null null null 0.0 null null null null null null null null null null null null null null null null null null 38878927920 683912412 2017-10-13T22:57:47.000+0000 help@goldstar.com 1 Goldstar Adult General Admission Plus Ice Slide Fast Pass 854871249 help@goldstar.com 2017-12-23T12:00:00.000+0000 United States null null null null 0.0 null null null null null null null null null null null null null null null null null null 38878927920 699142363 2017-11-16T22:30:13.000+0000 help@goldstar.com 1 Child General Admission Plus Ice Slide Fast Pass via Goldstar Comp Train 873325153 help@goldstar.com 2017-12-23T12:00:00.000+0000 United States null null null null 0.0 null null null null null null null null null null null null null null null null null null 38878927920 683912412 2017-10-13T22:57:47.000+0000 help@goldstar.com 1 Goldstar Adult General Admission Plus Ice Slide Fast Pass 854871300 help@goldstar.com 2017-12-23T12:00:00.000+0000 United States null null null null 0.0 null null null null null null null null null null null null null null null null null null 38878927920 683912412 2017-10-13T22:57:47.000+0000 help@goldstar.com 1 Goldstar Adult General Admission Plus Ice Slide Fast Pass 854871298 help@goldstar.com 2017-12-23T12:00:00.000+0000 United States null null null null 0.0 null null null null null null null null null null null null null null null null null null 38878927920 683912412 2017-10-13T22:57:47.000+0000 help@goldstar.com 1 Goldstar Adult General Admission Plus Ice Slide Fast Pass 854871299 help@goldstar.com 2017-12-23T12:00:00.000+0000 United States null null null null 0.0 null null null null null null null null null null null null null null null null null null 38878927920 683912412 2017-10-13T22:57:47.000+0000 help@goldstar.com 1 Goldstar Adult General Admission Plus Ice Slide Fast Pass 854871296 help@goldstar.com 2017-12-23T12:00:00.000+0000 United States null null null null 0.0 null null null null null null null null null null null null null null null null null null 38878927920 683912412 2017-10-13T22:57:47.000+0000 help@goldstar.com 1 Goldstar Adult General Admission Plus Ice Slide Fast Pass 854871297 help@goldstar.com 2017-12-23T12:00:00.000+0000 United States null null null null 0.0 null null null null null null null null null null null null null null null null null null 38878927920 683912412 2017-10-13T22:57:47.000+0000 help@goldstar.com 1 Goldstar Adult General Admission Plus Ice Slide Fast Pass 854871301 help@goldstar.com 2017-12-23T12:00:00.000+0000 United States null null null null 0.0 null null null null null null null null null null null null null null null null null null 38878927920 685589612 2017-10-17T21:25:39.000+0000 help@goldstar.com 1 Child General Admission Plus Ice Slide Fast Pass via Goldstar Comp Train 856943208 help@goldstar.com 2017-12-23T12:00:00.000+0000 United States null null null null 0.0 null null null null null null null null null null null null null null null null null null 38878927920 685589612 2017-10-17T21:25:39.000+0000 help@goldstar.com 1 Adult General Admission Plus Ice Slide Fast Pass via Goldstar Comp Train 856943141 help@goldstar.com 2017-12-23T12:00:00.000+0000 United States null null null null 0.0 null null null null null null null null null null null null null null null null null

In [0]:
%sql

delete from bronze_TcktSales_delta where order_location is null

num_affected_rows 12535

In [0]:
%sql
 
select count(*) from bronze_TcktSales_delta where order_location is null

count(1) 0

In [0]:
%sql

select * from bronze_TcktSales_delta where order_location like ' %' OR order_id like '% '

event_id order_id order_date email quantity ticket_type attendee_id buyer_email event_date order_city order_state order_country discount affiliate total_paid home_address_1 home_address_2 home_city home_state home_zip home_country what_are_you_most_excited_for_at_winter_fest_oc how_did_you_hear_about_winter_fest_oc have_you_attended_winter_fest_oc_before did_you_attend_winter_fest_oc_last_year billing_address_1 billing_address_2 billing_city billing_state billing_country billing_zip zip order_location


### Tests for attendee_id

In [0]:
%sql

select * from bronze_TcktSales_delta where attendee_id = 0

event_id order_id order_date email quantity ticket_type attendee_id buyer_email event_date order_city order_state order_country discount affiliate total_paid home_address_1 home_address_2 home_city home_state home_zip home_country what_are_you_most_excited_for_at_winter_fest_oc how_did_you_hear_about_winter_fest_oc have_you_attended_winter_fest_oc_before did_you_attend_winter_fest_oc_last_year billing_address_1 billing_address_2 billing_city billing_state billing_country billing_zip zip order_location

In [0]:
%sql

select * from bronze_TcktSales_delta where attendee_id is null

event_id order_id order_date email quantity ticket_type attendee_id buyer_email event_date order_city order_state order_country discount affiliate total_paid home_address_1 home_address_2 home_city home_state home_zip home_country what_are_you_most_excited_for_at_winter_fest_oc how_did_you_hear_about_winter_fest_oc have_you_attended_winter_fest_oc_before did_you_attend_winter_fest_oc_last_year billing_address_1 billing_address_2 billing_city billing_state billing_country billing_zip zip order_location

In [0]:
%sql

select * from bronze_TcktSales_delta where attendee_id like ' %' OR attendee_id like '% '

event_id order_id order_date email quantity ticket_type attendee_id buyer_email event_date order_city order_state order_country discount affiliate total_paid home_address_1 home_address_2 home_city home_state home_zip home_country what_are_you_most_excited_for_at_winter_fest_oc how_did_you_hear_about_winter_fest_oc have_you_attended_winter_fest_oc_before did_you_attend_winter_fest_oc_last_year billing_address_1 billing_address_2 billing_city billing_state billing_country billing_zip zip order_location

In [0]:
%sql

select * from bronze_TcktSales_delta where length(attendee_id) > 10

event_id order_id order_date email quantity ticket_type attendee_id buyer_email event_date order_city order_state order_country discount affiliate total_paid home_address_1 home_address_2 home_city home_state home_zip home_country what_are_you_most_excited_for_at_winter_fest_oc how_did_you_hear_about_winter_fest_oc have_you_attended_winter_fest_oc_before did_you_attend_winter_fest_oc_last_year billing_address_1 billing_address_2 billing_city billing_state billing_country billing_zip zip order_location


### Identifying Redundant/Unnecessary Columns


Some of the columns that I can instantly identify are not useful for my analysis are the "what_are_you_most_excited_for_at_winter_fest_oc", "how_did_you_hear_about_winter_fest_oc", "have_you_attended_winter_fest_oc_before", and "did_you_attend_winter_fest_oc_last_year". Also columns relating to billing addresses are not needed for my analysis, so they will be excluded from the silver layer as well. Another set of columns that are questionable due to their similarity to other columns include those relating to emails and zip codes.


### email and buyer_email columns

In [0]:
%sql

select count(*) from bronze_TcktSales_delta where buyer_email is not null

count(1) 159462

In [0]:
%sql

select count(*) from bronze_TcktSales_delta where email is not null

count(1) 159462

In [0]:
%sql

select count(*) from bronze_TcktSales_delta where email = buyer_email

count(1) 157086


As shown from the updated count of the bronze_TcktSales_delta, the total number of rows that are not null for both email and buyer_email is 159,462. Out of that, 157,086 of those rows consist of matching values between email and buyer_email. To figure out the exact percentage of this in order to assess whether or not keeping the two is redundant, I wrote the following Python script.

In [0]:
x = 157086
y = 159462
match_percentage = (x/y)*100
print("The percentage of matching values between the email and buyer email column is", match_percentage, '%')

The percentage of matching values between the email and buyer email column is 98.50998984083984 %



This indicates that roughly, 98.5% of emails between these two columns are matching, indicating that much of the data may prove redundant in later tables as the intention of both columns appeared to be to store the same information apart from a small amount of differences (1.5%). As a result, I have decided that it is not necessary to include both in the silver level tables and will only keep one with that being the "email" column.


### anonymized email rows


Also although it has nothing to do with cleaning data for use alongside potential key columns, I decided to remove anonymized data in the email/buyer_email columns. The reason for this is out of personal choice, as I wanted to only retain email addresses that were fully viewable for use in the silver layer and beyond.

In [0]:
%sql

delete from bronze_Tcktsales_delta where email like "%*%"

num_affected_rows 4


This removed four rows with email addresses containing the "*" symbol.


### home_zip and zip columns

In [0]:
%sql

select count(*) from bronze_TcktSales_delta where zip is not null

count(1) 51261

In [0]:
%sql

select count(*) from bronze_TcktSales_delta where home_zip is not null

count(1) 35446

In [0]:
%sql

select count(*) from bronze_TcktSales_delta where zip = home_zip

count(1) 34087

In [0]:
x = 34087
y = 35446
match_percentage = (x/y)*100
print("The percentage of matching values between the zip and buyer zip column is", match_percentage, '%')

The percentage of matching values between the zip and buyer zip column is 96.16599898437059 %



Given that 96% of these values match, it can be concluded that for the most part, they represent the same information. Meaning that both do not need to be included in the silver level tables.


Based on this, what I will do is pass data from the zip column to the silver layer because it contains more populated data and use it later on when creating the attendee_dimension.


### Final count of rows in bronze delta table following data cleaning

In [0]:
%sql

select count(*) from bronze_TcktSales_delta

count(1) 159458


### Silver Layer

In [0]:
%sql
 
drop table if exists fall_2023_finals.silver_TcktSales_delta_part1

In [0]:
%sql
CREATE TABLE fall_2023_finals.silver_TcktSales_delta_part1 (
  attendee_id INT,
  event_id BIGINT,
  order_id INT,
  order_date TIMESTAMP,
  email STRING,
  quantity INT,
  ticket_type STRING,
  event_date TIMESTAMP,
  order_location STRING,
  order_city STRING,
  order_state STRING,
  order_country STRING,
  discount STRING,
  affiliate STRING,
  total_paid DOUBLE,
  home_address_1 STRING,
  home_address_2 STRING,
  home_city STRING,
  home_state STRING,
  home_country STRING,
  zip INT)
USING delta
OPTIONS (
  'delimiter' = ',',
  'header' = 'true',
  'inferSchema' = 'true')
LOCATION 'dbfs:/mnt/mount/fall_2023_finals/TicketSales/silver/part1'

In [0]:
%sql
 
drop table if exists fall_2023_finals.silver_TcktSales_delta_part2

In [0]:
%sql
CREATE TABLE fall_2023_finals.silver_TcktSales_delta_part2 (
  attendee_id INT,
  event_id BIGINT,
  order_id INT,
  order_date TIMESTAMP,
  email STRING,
  quantity INT,
  ticket_type STRING,
  event_date TIMESTAMP,
  order_location STRING,
  order_city STRING,
  order_state STRING,
  order_country STRING,
  discount STRING,
  affiliate STRING,
  total_paid DOUBLE,
  home_address_1 STRING,
  home_address_2 STRING,
  home_city STRING,
  home_state STRING,
  home_country STRING,
  zip INT)
USING delta
OPTIONS (
  'delimiter' = ',',
  'header' = 'true',
  'inferSchema' = 'true')
LOCATION 'dbfs:/mnt/mount/fall_2023_finals/TicketSales/silver/part2'

In [0]:
%sql

insert into silver_TcktSales_delta_part1 (
    attendee_id, event_id, order_id, order_date, email, quantity,
    ticket_type, event_date, order_location,
    order_city, order_state, order_country, discount,
    affiliate, total_paid, home_address_1, home_address_2,
    home_city, home_state, home_country, zip
)
select
    attendee_id, event_id, order_id, order_date, email, quantity,
    ticket_type, event_date, order_location,
    order_city, order_state, order_country, discount,
    affiliate, total_paid, home_address_1, home_address_2,
    home_city, home_state, home_country, zip
from bronze_TcktSales_delta
limit 100;

num_affected_rows num_inserted_rows 100 100

In [0]:
%sql

insert into silver_TcktSales_delta_part2 (
    attendee_id, event_id, order_id, order_date, email, quantity,
    ticket_type, event_date, order_location,
    order_city, order_state, order_country, discount,
    affiliate, total_paid, home_address_1, home_address_2,
    home_city, home_state, home_country, zip
)
select
    attendee_id, event_id, order_id, order_date, email, quantity,
    ticket_type, event_date, order_location,
    order_city, order_state, order_country, discount,
    affiliate, total_paid, home_address_1, home_address_2,
    home_city, home_state, home_country, zip
from bronze_TcktSales_delta
offset 100;

num_affected_rows num_inserted_rows 159358 159358


### Viewing first 5 rows of both Silver tables

In [0]:
%sql

select * from silver_TcktSales_delta_part1 limit 5

attendee_id event_id order_id order_date email quantity ticket_type event_date order_location order_city order_state order_country discount affiliate total_paid home_address_1 home_address_2 home_city home_state home_country zip 885484430 38878678173 709113897 2017-12-17T00:20:18.000+0000 patty.delpilar.patty.delpilar.roman@gmail.com 1 Online Child General Admission (3 - 12 years old) 2017-12-21T17:00:00.000+0000 Santa Ana, CA, United States Santa Ana CA United States null erelpanelorg 15.69 null null null null null null 877795034 38878678173 702831510 2017-11-28T06:12:49.000+0000 classicquilting@gmail.com 1 Groupon: One Single-Day Child General Admission Pass and Snowflake Summit Ice Tubing Fast Pass 2017-12-21T17:00:00.000+0000 Costa Mesa, CA, United States Costa Mesa CA United States RTGYNBHP null 0.0 null null null null null null 886589873 38878678173 710021007 2017-12-21T00:15:05.000+0000 adv92867@hotmail.com 1 Online Platinum Ice Pass Presented By Orange County SC- Admission + Ice Skating + Unlimited Carnival Rides + Snowflake Summit Ice Tube Fast Pass + Orange County SC Ticket 2017-12-21T17:00:00.000+0000 Orange, CA, United States Orange CA United States null echckt 42.99 null null null null null null 886024400 38878678173 709554356 2017-12-19T05:35:07.000+0000 bgutierrez083@yahoo.com 1 Online Opening Hour Admission (5pm-6pm) 2017-12-21T17:00:00.000+0000 Fontana, CA, United States Fontana CA United States null echckt 13.59 null null null null null null 885607043 38878927920 709212340 2017-12-17T18:20:48.000+0000 the.espifamily@gmail.com 1 Online Platinum Ice Pass Presented By Orange County SC- Admission + Ice Skating + Unlimited Carnival Rides + Snowflake Summit Ice Tube Fast Pass + Orange County SC Ticket 2017-12-23T12:00:00.000+0000 Anaheim, CA, United States Anaheim CA United States null echckt 42.99 null null null null null null

In [0]:
%sql

select * from silver_TcktSales_delta_part2 limit 5

attendee_id event_id order_id order_date email quantity ticket_type event_date order_location order_city order_state order_country discount affiliate total_paid home_address_1 home_address_2 home_city home_state home_country zip 887394459 38878927920 710627233 2017-12-23T21:42:36.000+0000 wchamm@cox.net 1 Online Adult Admission 2017-12-23T12:00:00.000+0000 Trabuco Canyon, CA, United States Trabuco Canyon CA United States null echckt 20.94 null null null null null null 887394458 38878927920 710627233 2017-12-23T21:42:36.000+0000 wchamm@cox.net 1 Online Adult Admission 2017-12-23T12:00:00.000+0000 Trabuco Canyon, CA, United States Trabuco Canyon CA United States null echckt 20.94 null null null null null null 887425293 38878927920 710651252 2017-12-24T00:46:03.000+0000 atdorders+38878927920@eventbrite.com 1 At the Door Adult Admission 2017-12-23T12:00:00.000+0000 Hacienda Heights, CA, United States Hacienda Heights CA United States null BoxOffice 22.0 null null null null null null 886592530 38878678173 710023151 2017-12-21T00:26:34.000+0000 gavin900@gmail.com 1 Online Opening Hour Admission (5pm-6pm) 2017-12-21T17:00:00.000+0000 Torrance, CA, United States Torrance CA United States null echckt 13.59 null null null null null null 887425295 38878927920 710651252 2017-12-24T00:46:03.000+0000 atdorders+38878927920@eventbrite.com 1 At the Door Adult Admission 2017-12-23T12:00:00.000+0000 Hacienda Heights, CA, United States Hacienda Heights CA United States null BoxOffice 22.0 null null null null null null


### Creating Dimension and Fact Tables from Silver Table - Part 1


All fact and dimension tables created at this stage are stored in AWS S3.


### Dimension - Affiliate

In [0]:
%sql
drop table if exists dim_affiliate

In [0]:
%sql

create or replace table dim_affiliate (
affiliate_id BIGINT GENERATED BY DEFAULT AS IDENTITY (START WITH 1 INCREMENT BY 1),
affiliate STRING,
last_updated_on TIMESTAMP
)
using delta
LOCATION 'dbfs:/mnt/mount/fall_2023_finals/TicketSales/silver/dimaffiliate'


In order to handle null values and treat them as instances where no affiliate was involved, I used the COALESCE function to handle them appropritely and rename those instances to "No Affiliate"

In [0]:
%sql

insert into dim_affiliate(affiliate,last_updated_on) select distinct coalesce(affiliate, 'No Affiliate'), CURRENT_TIMESTAMP() from silver_TcktSales_delta_part1

num_affected_rows num_inserted_rows 5 5

In [0]:
%sql

select * from dim_affiliate limit 5

affiliate_id affiliate last_updated_on 1 erelpanelorg 2023-12-19T19:12:52.142+0000 2 BoxOffice 2023-12-19T19:12:52.142+0000 3 No Affiliate 2023-12-19T19:12:52.142+0000 4 echckt 2023-12-19T19:12:52.142+0000 5 erellivmlt 2023-12-19T19:12:52.142+0000


### Dimension - Ticket Type

In [0]:
%sql
drop table if exists dim_ticket_type

In [0]:
%sql

create or replace table dim_ticket_type (
ticket_type_id BIGINT GENERATED BY DEFAULT AS IDENTITY (START WITH 1 INCREMENT BY 1),
ticket_type STRING,
last_updated_on TIMESTAMP
)
using delta
LOCATION 'dbfs:/mnt/mount/fall_2023_finals/TicketSales/silver/dimtickettype'

In [0]:
%sql

insert into dim_ticket_type(ticket_type,last_updated_on) select distinct ticket_type, CURRENT_TIMESTAMP() from silver_TcktSales_delta_part1

num_affected_rows num_inserted_rows 14 14

In [0]:
%sql

select * from dim_ticket_type limit 5

ticket_type_id ticket_type last_updated_on 1 Promotion Day 2023-12-19T19:13:59.823+0000 2 Online Value (4) Pack for $65 - Admission + Snowflake Summit Fast Pass 2023-12-19T19:13:59.823+0000 3 At the Door Adult Admission 2023-12-19T19:13:59.823+0000 4 Onsite Platinum Ice Pass - Admission + Ice Skating + Unlimited Carnival Rides + Snowflake Summit Ice Tube Fast Pass 2023-12-19T19:13:59.823+0000 5 Groupon: One Single-Day Child General Admission Pass and Snowflake Summit Ice Tubing Fast Pass 2023-12-19T19:13:59.823+0000


### Dimension - Event

In [0]:
%sql

drop table if exists dim_event

In [0]:
%sql

create or replace table dim_event (
event_id BIGINT GENERATED BY DEFAULT AS IDENTITY (START WITH 1 INCREMENT BY 1),
event_number BIGINT,
event_date TIMESTAMP,
last_updated_on TIMESTAMP
)
using delta
LOCATION 'dbfs:/mnt/mount/fall_2023_finals/TicketSales/silver/dimevent'

In [0]:
%sql

insert into dim_event(event_number, event_date, last_updated_on) select distinct event_id, event_date, CURRENT_TIMESTAMP() from silver_TcktSales_delta_part1

num_affected_rows num_inserted_rows 2 2

In [0]:
%sql

select * from dim_event limit 5

event_id event_number event_date last_updated_on 1 38878678173 2017-12-21T17:00:00.000+0000 2023-12-19T19:15:08.505+0000 2 38878927920 2017-12-23T12:00:00.000+0000 2023-12-19T19:15:08.505+0000


### Dimension - Order Location

In [0]:
%sql
drop table if exists dim_order_location

In [0]:
%sql

create or replace table dim_order_location (
order_location_id BIGINT GENERATED BY DEFAULT AS IDENTITY (START WITH 1 INCREMENT BY 1),
order_location STRING,
order_city STRING,
order_state STRING,
order_country STRING,
last_updated_on TIMESTAMP
)
using delta
LOCATION 'dbfs:/mnt/mount/fall_2023_finals/TicketSales/silver/dimorderlocation'

In [0]:
%sql

insert into dim_order_location(order_location, order_city, order_state, order_country, last_updated_on) select distinct order_location, order_city, order_state, order_country, CURRENT_TIMESTAMP() from silver_TcktSales_delta_part1

num_affected_rows num_inserted_rows 21 21

In [0]:
%sql

select * from dim_order_location limit 5

order_location_id order_location order_city order_state order_country last_updated_on 1 Costa Mesa, CA, United States Costa Mesa CA United States 2023-12-19T19:16:21.342+0000 2 Montebello, CA, United States Montebello CA United States 2023-12-19T19:16:21.342+0000 3 Carson, CA, United States Carson CA United States 2023-12-19T19:16:21.342+0000 4 Hacienda Heights, CA, United States Hacienda Heights CA United States 2023-12-19T19:16:21.342+0000 5 Santa Ana, CA, United States Santa Ana CA United States 2023-12-19T19:16:21.342+0000


### Dimension - Attendee

In [0]:
%sql

drop table if exists dim_attendee

In [0]:
%sql

create or replace table dim_attendee (
attendee_id BIGINT GENERATED BY DEFAULT AS IDENTITY (START WITH 1 INCREMENT BY 1),
attendee_number INT,
email STRING,
home_address_1 STRING,
home_address_2 STRING,
home_city STRING,
home_state STRING,
home_country STRING,
zip INT,
last_updated_on TIMESTAMP
)
using delta
LOCATION 'dbfs:/mnt/mount/fall_2023_finals/TicketSales/silver/dimattendee'

In [0]:
%sql

insert into dim_attendee(attendee_number, email, home_address_1, home_address_2, home_city, home_state, home_country, zip, last_updated_on) select distinct attendee_id, email, home_address_1, home_address_2, home_city, home_state, home_country, zip, CURRENT_TIMESTAMP() from silver_TcktSales_delta_part1

num_affected_rows num_inserted_rows 100 100

In [0]:
%sql

select * from dim_attendee limit 5

attendee_id attendee_number email home_address_1 home_address_2 home_city home_state home_country zip last_updated_on 1 887424282 atdorders+38878927920@eventbrite.com null null null null null null 2023-12-19T19:19:32.358+0000 2 886969910 atdorders+38878678173@eventbrite.com null null null null null null 2023-12-19T19:19:32.358+0000 3 870996321 u133209@yahoo.com null null null null null null 2023-12-19T19:19:32.358+0000 4 887423900 atdorders+38878927920@eventbrite.com null null null null null null 2023-12-19T19:19:32.358+0000 5 885291167 a.palma88lb@gmail.com null null null null null null 2023-12-19T19:19:32.358+0000


### Dimension - Date

In [0]:
%sql

drop table if exists dim_date

In [0]:
%sql

create or replace table dim_date (
date_id BIGINT GENERATED BY DEFAULT AS IDENTITY (START WITH 1 INCREMENT BY 1),
order_date TIMESTAMP,
shortdate STRING,
day INT,
day_name STRING,
month INT,
month_name STRING,
week_of_month INT,
year INT,
week_of_year INT,
quarter_number INT,
is_weekend BOOLEAN,
last_updated_on TIMESTAMP
)
using delta
LOCATION 'dbfs:/mnt/mount/fall_2023_finals/TicketSales/silver/dimdate'

In [0]:
%sql
insert into dim_date (order_date, shortdate, day, day_name, month, month_name, week_of_month, year, week_of_year, quarter_number, is_weekend, last_updated_on)
select distinct
  order_date as order_date,
  date_format(order_date, 'MM-dd-yyyy') as shortdate,
  day(order_date) as day,
  date_format(order_date, 'EEEE') as day_name,
  month(order_date) as month,
  date_format(order_date, 'MMMM') as month_name,
  floor((day(order_date) - 1) / 7) + 1 as week_of_month,
  year(order_date) as year,
  weekofyear(order_date) as week_of_year,
  quarter(order_date) as quarter_number,
  dayofweek(order_date) in (1, 7) as is_weekend,
  CURRENT_TIMESTAMP() as last_updated_on
FROM
  silver_TcktSales_delta_part1

num_affected_rows num_inserted_rows 40 40

In [0]:
%sql

select * from dim_date limit 5

date_id order_date shortdate day day_name month month_name week_of_month year week_of_year quarter_number is_weekend last_updated_on 1 2017-12-17T18:27:44.000+0000 12-17-2017 17 Sunday 12 December 3 2017 50 4 true 2023-12-19T19:20:41.138+0000 2 2017-12-19T19:33:52.000+0000 12-19-2017 19 Tuesday 12 December 3 2017 51 4 false 2023-12-19T19:20:41.138+0000 3 2017-12-23T22:19:30.000+0000 12-23-2017 23 Saturday 12 December 4 2017 51 4 true 2023-12-19T19:20:41.138+0000 4 2017-12-03T03:06:57.000+0000 12-03-2017 3 Sunday 12 December 1 2017 48 4 true 2023-12-19T19:20:41.138+0000 5 2017-12-10T01:11:18.000+0000 12-10-2017 10 Sunday 12 December 2 2017 49 4 true 2023-12-19T19:20:41.138+0000


### Fact - Order Transaction


At this stage, I was testing the data for which I would use to build the fact table by first creating a regular table called fact_test prior to creating my external fact table in AWS S3. In order to prevent nulls in my fact table, I used the COALESCE function to handle them appropriately.

In [0]:
%sql
drop table if exists fact_test

In [0]:
%sql
create or replace table fact_test as
select distinct 
  e.event_id,
  a.attendee_id,
  coalesce(af.affiliate_id, 3) as affiliate_id,
  ord.order_location_id,
  tk.ticket_type_id,
  d.date_id,
  s.order_id,
  coalesce(s.discount, 'No Discount') as discount,
  s.total_paid,
  s.quantity,
  CURRENT_TIMESTAMP() as last_updated_on
from
  silver_TcktSales_delta_part1 s
  left join dim_attendee a on s.attendee_id = a.attendee_number
  left join dim_event e on s.event_id = e.event_number
  left join dim_affiliate af on s.affiliate = af.affiliate
  left join dim_order_location ord on s.order_location = ord.order_location
  left join dim_ticket_type tk on s.ticket_type = tk.ticket_type
  left join dim_date d on s.order_date = d.order_date;

num_affected_rows num_inserted_rows

In [0]:
%sql
select * from fact_test limit 5

event_id attendee_id affiliate_id order_location_id ticket_type_id date_id order_id discount total_paid quantity last_updated_on 2 57 2 4 13 31 710646755 No Discount 15.0 1 2023-12-19T19:21:30.574+0000 2 95 3 14 6 30 707872200 No Discount 20.94 1 2023-12-19T19:21:30.574+0000 2 91 3 2 14 4 704837023 No Discount 42.99 1 2023-12-19T19:21:30.574+0000 1 52 2 4 1 8 710289181 No Discount 0.0 1 2023-12-19T19:21:30.574+0000 2 43 2 4 3 24 710650454 No Discount 22.0 1 2023-12-19T19:21:30.574+0000

In [0]:
%sql
describe fact_test

col_name data_type comment event_id bigint null attendee_id bigint null affiliate_id bigint null order_location_id bigint null ticket_type_id bigint null date_id bigint null order_id int null discount string null total_paid double null quantity int null last_updated_on timestamp null

After this information was acquired, I created my external fact table in a similar way.

In [0]:
%sql

drop table if exists fact_order_transaction

In [0]:
%sql

create or replace table fact_order_transaction (
order_transaction_id BIGINT GENERATED BY DEFAULT AS IDENTITY (START WITH 1 INCREMENT BY 1),
event_id BIGINT,
attendee_id INT,
affiliate_id BIGINT,
order_location_id BIGINT,
ticket_type_id BIGINT,
date_id STRING,
order_id INT,
discount STRING,
total_paid DOUBLE,
quantity INT,
last_updated_on TIMESTAMP
)
using delta
LOCATION 'dbfs:/mnt/mount/fall_2023_finals/TicketSales/silver/factorder'

In [0]:
%sql

insert into fact_order_transaction
(event_id, attendee_id, affiliate_id, order_location_id, ticket_type_id, date_id, order_id, discount, total_paid, quantity, last_updated_on)
select distinct 
  e.event_id,
  a.attendee_id,
  COALESCE(af.affiliate_id, 3) as affiliate_id,
  ord.order_location_id,
  tk.ticket_type_id,
  d.date_id,
  s.order_id,
  COALESCE(s.discount, 'No Discount') as discount,
  s.total_paid,
  s.quantity,
  CURRENT_TIMESTAMP() as last_updated_on
from
  silver_TcktSales_delta_part1 s
  left join dim_attendee a on s.attendee_id = a.attendee_number
  left join dim_event e on s.event_id = e.event_number
  left join dim_affiliate af on s.affiliate = af.affiliate
  left join dim_order_location ord on s.order_location = ord.order_location
  left join dim_ticket_type tk on s.ticket_type = tk.ticket_type
  left join dim_date d on s.order_date = d.order_date;

num_affected_rows num_inserted_rows 100 100

In [0]:
%sql

select * from fact_order_transaction limit 5

order_transaction_id event_id attendee_id affiliate_id order_location_id ticket_type_id date_id order_id discount total_paid quantity last_updated_on 1 2 57 2 4 13 31 710646755 No Discount 15.0 1 2023-12-19T19:22:30.518+0000 2 2 95 3 14 6 30 707872200 No Discount 20.94 1 2023-12-19T19:22:30.518+0000 3 2 91 3 2 14 4 704837023 No Discount 42.99 1 2023-12-19T19:22:30.518+0000 4 1 52 2 4 1 8 710289181 No Discount 0.0 1 2023-12-19T19:22:30.518+0000 5 2 43 2 4 3 24 710650454 No Discount 22.0 1 2023-12-19T19:22:30.518+0000


### Dimension - Month

In [0]:
%sql
drop table if exists dim_month

In [0]:
%sql

create or replace table dim_month (
month_id BIGINT GENERATED BY DEFAULT AS IDENTITY (START WITH 1 INCREMENT BY 1),
order_date TIMESTAMP,
month INT,
month_name STRING,
week_of_month INT,
year INT,
quarter_number INT,
last_updated_on TIMESTAMP
)
using delta
LOCATION 'dbfs:/mnt/mount/fall_2023_finals/TicketSales/silver/dimmonth'

In [0]:
%sql
insert into dim_month (order_date, month, month_name, week_of_month, year, quarter_number, last_updated_on)
select distinct
  order_date as order_date,
  month(order_date) as month,
  date_format(order_date, 'MMMM') as month_name,
  floor((day(order_date) - 1) / 7) + 1 as week_of_month,
  year(order_date) as year,
  quarter(order_date) as quarter_number,
  CURRENT_TIMESTAMP() as last_updated_on
FROM
  silver_TcktSales_delta_part1

num_affected_rows num_inserted_rows 40 40

In [0]:
%sql
select * from dim_month limit 5

month_id order_date month month_name week_of_month year quarter_number last_updated_on 1 2017-12-17T18:20:48.000+0000 12 December 3 2017 4 2023-12-19T19:23:32.754+0000 2 2017-12-17T18:27:44.000+0000 12 December 3 2017 4 2023-12-19T19:23:32.754+0000 3 2017-12-11T05:16:06.000+0000 12 December 2 2017 4 2023-12-19T19:23:32.754+0000 4 2017-12-18T22:44:10.000+0000 12 December 3 2017 4 2023-12-19T19:23:32.754+0000 5 2017-12-24T00:10:28.000+0000 12 December 4 2017 4 2023-12-19T19:23:32.754+0000


### Fact - Monthly Sales

In [0]:
%sql
drop table if exists fact_monthly_sales

In [0]:
%sql

create or replace table fact_monthly_sales (
monthly_sales_id BIGINT GENERATED BY DEFAULT AS IDENTITY (START WITH 1 INCREMENT BY 1),
month_id BIGINT,
discount STRING,
total_paid DOUBLE,
quantity INT,
last_updated_on TIMESTAMP
)
using delta
LOCATION 'dbfs:/mnt/mount/fall_2023_finals/TicketSales/silver/factmonth'

In [0]:
%sql

insert into fact_monthly_sales
(month_id, discount, total_paid, quantity, last_updated_on)
select distinct
  m.month_id,
  COALESCE(s.discount, 'No Discount') as discount,
  s.total_paid,
  s.quantity,
  CURRENT_TIMESTAMP() as last_updated_on
from
  silver_TcktSales_delta_part1 s
  left join dim_month m on s.order_date = m.order_date

num_affected_rows num_inserted_rows 47 47

In [0]:
%sql
select * from fact_monthly_sales limit 5

monthly_sales_id month_id discount total_paid quantity last_updated_on 1 21 No Discount 20.94 1 2023-12-19T19:24:30.852+0000 2 11 No Discount 42.99 1 2023-12-19T19:24:30.852+0000 3 13 No Discount 45.0 1 2023-12-19T19:24:30.852+0000 4 37 RTGYNBHP 0.0 1 2023-12-19T19:24:30.852+0000 5 13 No Discount 22.0 1 2023-12-19T19:24:30.852+0000


### Dimension - Week

In [0]:
%sql
drop table if exists dim_week

In [0]:
%sql

create or replace table dim_week (
week_id BIGINT GENERATED BY DEFAULT AS IDENTITY (START WITH 1 INCREMENT BY 1),
order_date TIMESTAMP,
week_of_month INT,
year INT,
quarter_number INT,
last_updated_on TIMESTAMP
)
using delta
LOCATION 'dbfs:/mnt/mount/fall_2023_finals/TicketSales/silver/dimweek'

In [0]:
%sql
insert into dim_week (order_date, week_of_month, year, quarter_number, last_updated_on)
select distinct
  order_date as order_date,
  floor((day(order_date) - 1) / 7) + 1 as week_of_month,
  year(order_date) as year,
  quarter(order_date) as quarter_number,
  CURRENT_TIMESTAMP() as last_updated_on
FROM
  silver_TcktSales_delta_part1

num_affected_rows num_inserted_rows 40 40

In [0]:
%sql

select * from dim_week limit 5

week_id order_date week_of_month year quarter_number last_updated_on 1 2017-12-17T18:27:44.000+0000 3 2017 4 2023-12-19T19:25:31.742+0000 2 2017-12-23T02:20:41.000+0000 4 2017 4 2023-12-19T19:25:31.742+0000 3 2017-12-16T04:16:08.000+0000 3 2017 4 2023-12-19T19:25:31.742+0000 4 2017-11-29T18:24:23.000+0000 5 2017 4 2023-12-19T19:25:31.742+0000 5 2017-12-23T16:00:25.000+0000 4 2017 4 2023-12-19T19:25:31.742+0000


### Fact - Weekly Sales

In [0]:
%sql
drop table if exists fact_weekly_sales

In [0]:
%sql

create or replace table fact_weekly_sales (
weekly_sales_id BIGINT GENERATED BY DEFAULT AS IDENTITY (START WITH 1 INCREMENT BY 1),
week_id BIGINT,
discount STRING,
total_paid DOUBLE,
quantity INT,
last_updated_on TIMESTAMP
)
using delta
LOCATION 'dbfs:/mnt/mount/fall_2023_finals/TicketSales/silver/factweek'

In [0]:
%sql

insert into fact_weekly_sales
(week_id, discount, total_paid, quantity, last_updated_on)
select distinct
  w.week_id,
  COALESCE(s.discount, 'No Discount') as discount,
  s.total_paid,
  s.quantity,
  CURRENT_TIMESTAMP() as last_updated_on
from
  silver_TcktSales_delta_part1 s
  left join dim_week w on s.order_date = w.order_date

num_affected_rows num_inserted_rows 47 47

In [0]:
%sql
select * from fact_weekly_sales limit 5

weekly_sales_id week_id discount total_paid quantity last_updated_on 1 16 No Discount 42.99 1 2023-12-19T19:26:36.875+0000 2 18 No Discount 20.94 1 2023-12-19T19:26:36.875+0000 3 36 No Discount 22.0 1 2023-12-19T19:26:36.875+0000 4 31 No Discount 20.16 1 2023-12-19T19:26:36.875+0000 5 15 No Discount 42.99 1 2023-12-19T19:26:36.875+0000


### Merging Dimension & Fact Tables with Silver Table Data - Part 2

### Dimension - Affiliate

In [0]:
%sql
create or replace temporary view vw_newaffiliate_temp as 
  select affiliate,current_timestamp() as last_updated_on from (
    select distinct(affiliate) from fall_2023_finals.silver_TcktSales_delta_part2
    minus
    select affiliate from dim_affiliate 
)

In [0]:
%sql
select * from vw_newaffiliate_temp limit 5

affiliate last_updated_on null 2023-12-19T19:27:43.233+0000 efbeventtix 2023-12-19T19:27:43.233+0000 eand 2023-12-19T19:27:43.233+0000 ehomecard 2023-12-19T19:27:43.233+0000 eios 2023-12-19T19:27:43.233+0000

In [0]:
%sql
Merge into dim_affiliate a using vw_newaffiliate_temp ta
on a.affiliate = ta.affiliate
when not matched then insert (affiliate,last_updated_on) values(ta.affiliate,ta.last_updated_on)

num_affected_rows num_updated_rows num_deleted_rows num_inserted_rows 33 0 0 33

In [0]:
%sql
select * from dim_affiliate limit 5

affiliate_id affiliate last_updated_on 1 erelpanelorg 2023-12-19T19:12:52.142+0000 2 BoxOffice 2023-12-19T19:12:52.142+0000 3 No Affiliate 2023-12-19T19:12:52.142+0000 4 echckt 2023-12-19T19:12:52.142+0000 5 erellivmlt 2023-12-19T19:12:52.142+0000

### Dimension - Ticket Type

In [0]:
%sql
create or replace temporary view vw_newticket_type_temp as 
  select ticket_type,current_timestamp() as last_updated_on from (
    select distinct(ticket_type) from fall_2023_finals.silver_TcktSales_delta_part2
    minus
    select ticket_type from dim_ticket_type 
)

In [0]:
%sql
select * from vw_newticket_type_temp limit 5

ticket_type last_updated_on Ice Skating (Purchased Platinum) 5:15pm - 6:00pm 2023-12-19T19:27:59.411+0000 Group Children Admission (3 - 12 years old) for 10 or more 2023-12-19T19:27:59.411+0000 Online Child Admission (3 - 12 years old) 2023-12-19T19:27:59.411+0000 Online Platinum Ice Pass - Admission + Ice Skating + Unlimited Carnival Rides + Snowflake Summit Ice Tube Fast Pass 2023-12-19T19:27:59.411+0000 Online Unlimited Ride Wristband 2023-12-19T19:27:59.411+0000

In [0]:
%sql
Merge into dim_ticket_type t using vw_newticket_type_temp tt
on t.ticket_type = tt.ticket_type
when not matched then insert (ticket_type,last_updated_on) values(tt.ticket_type,tt.last_updated_on)

num_affected_rows num_updated_rows num_deleted_rows num_inserted_rows 313 0 0 313

In [0]:
%sql
select * from dim_ticket_type limit 5

ticket_type_id ticket_type last_updated_on 1 Promotion Day 2023-12-19T19:13:59.823+0000 2 Online Value (4) Pack for $65 - Admission + Snowflake Summit Fast Pass 2023-12-19T19:13:59.823+0000 3 At the Door Adult Admission 2023-12-19T19:13:59.823+0000 4 Onsite Platinum Ice Pass - Admission + Ice Skating + Unlimited Carnival Rides + Snowflake Summit Ice Tube Fast Pass 2023-12-19T19:13:59.823+0000 5 Groupon: One Single-Day Child General Admission Pass and Snowflake Summit Ice Tubing Fast Pass 2023-12-19T19:13:59.823+0000

### Dimension - Event

In [0]:
%sql
create or replace temporary view vw_newevent_temp as 
  select event_id,current_timestamp() as last_updated_on from (
    select distinct(event_id) from fall_2023_finals.silver_TcktSales_delta_part2
    minus
    select event_number from dim_event 
)

In [0]:
%sql
select * from vw_newevent_temp limit 5

event_id last_updated_on 38880142553 2023-12-19T19:28:13.724+0000 38878878773 2023-12-19T19:28:13.724+0000 38879213775 2023-12-19T19:28:13.724+0000 38879122502 2023-12-19T19:28:13.724+0000 38880176655 2023-12-19T19:28:13.724+0000

In [0]:
%sql
Merge into dim_event e using vw_newevent_temp et
on e.event_number = et.event_id
when not matched then insert (event_number,last_updated_on) values(et.event_id,et.last_updated_on)

num_affected_rows num_updated_rows num_deleted_rows num_inserted_rows 36 0 0 36

In [0]:
%sql
select * from dim_event limit 5

event_id event_number event_date last_updated_on 3 38880233826 null 2023-12-19T19:28:17.235+0000 4 38880142553 null 2023-12-19T19:28:17.235+0000 5 48207584182 null 2023-12-19T19:28:17.235+0000 6 48207597221 null 2023-12-19T19:28:17.235+0000 7 51496438233 null 2023-12-19T19:28:17.235+0000


### Dimension - Order Location

In [0]:
%sql
create or replace temporary view vw_neworder_temp as 
  select order_location,current_timestamp() as last_updated_on from (
    select distinct(order_location) from fall_2023_finals.silver_TcktSales_delta_part2
    minus
    select order_location from dim_order_location 
)

In [0]:
%sql
select * from vw_neworder_temp limit 5

order_location last_updated_on Tustin, CA, United States 2023-12-19T19:28:28.226+0000 Pacoima, CA, United States 2023-12-19T19:28:28.226+0000 Hemet, CA, United States 2023-12-19T19:28:28.226+0000 Santa Monica, CA, United States 2023-12-19T19:28:28.226+0000 Rancho Cucamonga, CA, United States 2023-12-19T19:28:28.226+0000

In [0]:
%sql
Merge into dim_order_location ord using vw_neworder_temp tor
on ord.order_location = tor.order_location
when not matched then insert (order_location,last_updated_on) values(tor.order_location,tor.last_updated_on)

num_affected_rows num_updated_rows num_deleted_rows num_inserted_rows 517 0 0 517

In [0]:
%sql
select * from dim_order_location limit 5

order_location_id order_location order_city order_state order_country last_updated_on 1 Costa Mesa, CA, United States Costa Mesa CA United States 2023-12-19T19:16:21.342+0000 2 Montebello, CA, United States Montebello CA United States 2023-12-19T19:16:21.342+0000 3 Carson, CA, United States Carson CA United States 2023-12-19T19:16:21.342+0000 4 Hacienda Heights, CA, United States Hacienda Heights CA United States 2023-12-19T19:16:21.342+0000 5 Santa Ana, CA, United States Santa Ana CA United States 2023-12-19T19:16:21.342+0000


### Dimension - Attendee

In [0]:
%sql
create or replace temporary view vw_newattendee_temp as 
  select attendee_id,current_timestamp() as last_updated_on from (
    select distinct(attendee_id) from fall_2023_finals.silver_TcktSales_delta_part2
    minus
    select attendee_number from dim_attendee 
)

In [0]:
%sql
select * from vw_newattendee_temp limit 5

attendee_id last_updated_on 1091643361 2023-12-19T19:28:41.501+0000 1093122223 2023-12-19T19:28:41.501+0000 1095642110 2023-12-19T19:28:41.501+0000 1077225895 2023-12-19T19:28:41.501+0000 1092455156 2023-12-19T19:28:41.501+0000

In [0]:
%sql
Merge into dim_attendee att using vw_newattendee_temp tatt
on att.attendee_number = tatt.attendee_id
when not matched then insert (attendee_number,last_updated_on) values(tatt.attendee_id,tatt.last_updated_on)

num_affected_rows num_updated_rows num_deleted_rows num_inserted_rows 159358 0 0 159358

In [0]:
%sql
select * from dim_attendee limit 5

attendee_id attendee_number email home_address_1 home_address_2 home_city home_state home_country zip last_updated_on 1 887424282 atdorders+38878927920@eventbrite.com null null null null null null 2023-12-19T19:19:32.358+0000 2 886969910 atdorders+38878678173@eventbrite.com null null null null null null 2023-12-19T19:19:32.358+0000 3 870996321 u133209@yahoo.com null null null null null null 2023-12-19T19:19:32.358+0000 4 887423900 atdorders+38878927920@eventbrite.com null null null null null null 2023-12-19T19:19:32.358+0000 5 885291167 a.palma88lb@gmail.com null null null null null null 2023-12-19T19:19:32.358+0000

### Dimension - Date

In [0]:
%sql
create or replace temporary view vw_newdate_temp as 
  select order_date,current_timestamp() as last_updated_on from (
    select distinct(order_date) from fall_2023_finals.silver_TcktSales_delta_part2
    minus
    select order_date from dim_date 
)

In [0]:
%sql
select * from vw_newdate_temp limit 5

order_date last_updated_on 2017-12-21T00:26:34.000+0000 2023-12-19T19:28:56.415+0000 2017-12-23T22:29:36.000+0000 2023-12-19T19:28:56.415+0000 2017-12-20T01:56:37.000+0000 2023-12-19T19:28:56.415+0000 2017-12-24T00:46:03.000+0000 2023-12-19T19:28:56.415+0000 2017-12-01T01:36:53.000+0000 2023-12-19T19:28:56.415+0000

In [0]:
%sql
Merge into dim_date d using vw_newdate_temp nd
on d.order_date = nd.order_date
when not matched then insert (order_date,last_updated_on) values(nd.order_date,nd.last_updated_on)

num_affected_rows num_updated_rows num_deleted_rows num_inserted_rows 64598 0 0 64598

In [0]:
%sql
select * from dim_date limit 5

date_id order_date shortdate day day_name month month_name week_of_month year week_of_year quarter_number is_weekend last_updated_on 1 2017-12-17T18:27:44.000+0000 12-17-2017 17 Sunday 12 December 3 2017 50 4 true 2023-12-19T19:20:41.138+0000 2 2017-12-19T19:33:52.000+0000 12-19-2017 19 Tuesday 12 December 3 2017 51 4 false 2023-12-19T19:20:41.138+0000 3 2017-12-23T22:19:30.000+0000 12-23-2017 23 Saturday 12 December 4 2017 51 4 true 2023-12-19T19:20:41.138+0000 4 2017-12-03T03:06:57.000+0000 12-03-2017 3 Sunday 12 December 1 2017 48 4 true 2023-12-19T19:20:41.138+0000 5 2017-12-10T01:11:18.000+0000 12-10-2017 10 Sunday 12 December 2 2017 49 4 true 2023-12-19T19:20:41.138+0000


### Fact - Order Transaction

In [0]:
%sql
create or replace temporary view vw_order_transaction as
select distinct
  e.event_id,
  a.attendee_id,
  COALESCE(af.affiliate_id, 3) as affiliate_id,
  ord.order_location_id,
  tk.ticket_type_id,
  d.date_id,
  s.order_id,
  COALESCE(s.discount, 'No Discount') as discount,
  s.total_paid,
  s.quantity,
  CURRENT_TIMESTAMP() as last_updated_on
from
  silver_TcktSales_delta_part2 s
  left join dim_attendee a on s.attendee_id = a.attendee_number
  left join dim_event e on s.event_id = e.event_number
  left join dim_affiliate af on s.affiliate = af.affiliate
  left join dim_order_location ord on s.order_location = ord.order_location
  left join dim_ticket_type tk on s.ticket_type = tk.ticket_type
  left join dim_date d on s.order_date = d.order_date;

In [0]:
%sql
select * from vw_order_transaction limit 5

event_id attendee_id affiliate_id order_location_id ticket_type_id date_id order_id discount total_paid quantity last_updated_on 2 69555 4 9 8 6646 710062319 No Discount 13.59 1 2023-12-19T19:29:12.412+0000 2 123688 4 380 2 64289 710613714 No Discount 20.16 1 2023-12-19T19:29:12.412+0000 2 73584 4 10 14 33051 710652911 No Discount 42.99 1 2023-12-19T19:29:12.412+0000 2 44251 2 4 7 61121 710652025 No Discount 17.0 1 2023-12-19T19:29:12.412+0000 2 141374 4 333 6 53650 710652285 No Discount 20.94 1 2023-12-19T19:29:12.412+0000

In [0]:
%sql
Merge into fact_order_transaction f using vw_order_transaction t
on f.event_id = t.event_id AND f.attendee_id = t.attendee_id and f.affiliate_id = t.affiliate_id and f.order_location_id = t.order_location_id 
and f.ticket_type_id = t.ticket_type_id and f.date_id = t.date_id
when matched then 
update set
  f.event_id = t.event_id
  ,f.attendee_id = t.attendee_id
  ,f.affiliate_id = t.affiliate_id
  ,f.order_location_id = t.order_location_id
  ,f.ticket_type_id = t.ticket_type_id
  ,f.date_id = t.date_id
  ,f.order_id = t.order_id
  ,f.discount = t.discount
  ,f.total_paid = t.total_paid
  ,f.quantity = t.quantity
  ,f.last_updated_on = t.last_updated_on

when not matched then insert
  (
    event_id
    ,attendee_id
    ,affiliate_id
    ,order_location_id
    ,ticket_type_id
    ,date_id
    ,order_id
    ,discount
    ,total_paid
    ,quantity
    ,last_updated_on
  ) values
  (
    t.event_id
    ,t.attendee_id
    ,t.affiliate_id
    ,t.order_location_id
    ,t.ticket_type_id
    ,t.date_id
    ,t.order_id
    ,t.discount
    ,t.total_paid
    ,t.quantity
    ,t.last_updated_on
  )

num_affected_rows num_updated_rows num_deleted_rows num_inserted_rows 159358 0 0 159358

In [0]:
%sql
select * from fact_order_transaction limit 5

order_transaction_id event_id attendee_id affiliate_id order_location_id ticket_type_id date_id order_id discount total_paid quantity last_updated_on 1 2 57 2 4 13 31 710646755 No Discount 15.0 1 2023-12-19T19:22:30.518+0000 2 2 95 3 14 6 30 707872200 No Discount 20.94 1 2023-12-19T19:22:30.518+0000 3 2 91 3 2 14 4 704837023 No Discount 42.99 1 2023-12-19T19:22:30.518+0000 4 1 52 2 4 1 8 710289181 No Discount 0.0 1 2023-12-19T19:22:30.518+0000 5 2 43 2 4 3 24 710650454 No Discount 22.0 1 2023-12-19T19:22:30.518+0000


### Dimension - Month

In [0]:
%sql
create or replace temporary view vw_newmonth_temp as 
  select order_date,current_timestamp() as last_updated_on from (
    select distinct(order_date) from fall_2023_finals.silver_TcktSales_delta_part2
    minus
    select order_date from dim_month 
)

In [0]:
%sql
select * from vw_newmonth_temp limit 5

order_date last_updated_on 2017-12-21T00:26:34.000+0000 2023-12-19T19:29:44.985+0000 2017-12-23T22:29:36.000+0000 2023-12-19T19:29:44.985+0000 2017-12-20T01:56:37.000+0000 2023-12-19T19:29:44.985+0000 2017-12-24T00:46:03.000+0000 2023-12-19T19:29:44.985+0000 2017-12-01T01:36:53.000+0000 2023-12-19T19:29:44.985+0000

In [0]:
%sql
Merge into dim_month m using vw_newmonth_temp nm
on m.order_date = nm.order_date
when not matched then insert (order_date,last_updated_on) values(nm.order_date,nm.last_updated_on)

num_affected_rows num_updated_rows num_deleted_rows num_inserted_rows 64598 0 0 64598

In [0]:
%sql
select * from dim_month limit 5

month_id order_date month month_name week_of_month year quarter_number last_updated_on 1 2017-12-17T18:20:48.000+0000 12 December 3 2017 4 2023-12-19T19:23:32.754+0000 2 2017-12-17T18:27:44.000+0000 12 December 3 2017 4 2023-12-19T19:23:32.754+0000 3 2017-12-11T05:16:06.000+0000 12 December 2 2017 4 2023-12-19T19:23:32.754+0000 4 2017-12-18T22:44:10.000+0000 12 December 3 2017 4 2023-12-19T19:23:32.754+0000 5 2017-12-24T00:10:28.000+0000 12 December 4 2017 4 2023-12-19T19:23:32.754+0000


### Fact - Monthly Sales

In [0]:
%sql
create or replace temporary view vw_monthly_sales as
select distinct
  m.month_id,
  COALESCE(s.discount, 'No Discount') as discount,
  s.total_paid,
  s.quantity,
  CURRENT_TIMESTAMP() as last_updated_on
from
  silver_TcktSales_delta_part2 s
  left join dim_month m on s.order_date = m.order_date

In [0]:
%sql
select * from vw_monthly_sales limit 5

month_id discount total_paid quantity last_updated_on 14382 No Discount 42.99 1 2023-12-19T22:31:50.057+0000 45196 No Discount 22.0 1 2023-12-19T22:31:50.057+0000 53318 No Discount 17.0 1 2023-12-19T22:31:50.057+0000 47027 No Discount 20.94 1 2023-12-19T22:31:50.057+0000 40694 No Discount 0.0 1 2023-12-19T22:31:50.057+0000

In [0]:
%sql
merge into fact_monthly_sales f using vw_monthly_sales t
on f.month_id = t.month_id and f.discount = t.discount and f.total_paid = t.total_paid and f.quantity = t.quantity and f.last_updated_on = t.last_updated_on
when matched then 
  update set
    f.month_id = t.month_id,
    f.discount = t.discount,
    f.total_paid = t.total_paid,
    f.quantity = t.quantity,
    f.last_updated_on = t.last_updated_on
when not matched then 
  insert (
    month_id,
    discount,
    total_paid,
    quantity,
    last_updated_on
  ) values (
    t.month_id,
    t.discount,
    t.total_paid,
    t.quantity,
    t.last_updated_on
  );

num_affected_rows num_updated_rows num_deleted_rows num_inserted_rows 80402 0 0 80402

In [0]:
%sql
select * from fact_monthly_sales limit 5

monthly_sales_id month_id discount total_paid quantity last_updated_on 1 21 No Discount 20.94 1 2023-12-19T19:24:30.852+0000 2 11 No Discount 42.99 1 2023-12-19T19:24:30.852+0000 3 13 No Discount 45.0 1 2023-12-19T19:24:30.852+0000 4 37 RTGYNBHP 0.0 1 2023-12-19T19:24:30.852+0000 5 13 No Discount 22.0 1 2023-12-19T19:24:30.852+0000


### Dimension - Week

In [0]:
%sql
create or replace temporary view vw_newweek_temp as 
  select order_date,current_timestamp() as last_updated_on from (
    select distinct(order_date) from fall_2023_finals.silver_TcktSales_delta_part2
    minus
    select order_date from dim_week 
)

In [0]:
%sql
select * from vw_newweek_temp limit 5

order_date last_updated_on 2017-12-21T00:26:34.000+0000 2023-12-19T19:30:14.347+0000 2017-12-23T22:29:36.000+0000 2023-12-19T19:30:14.347+0000 2017-12-20T01:56:37.000+0000 2023-12-19T19:30:14.347+0000 2017-12-24T00:46:03.000+0000 2023-12-19T19:30:14.347+0000 2017-12-01T01:36:53.000+0000 2023-12-19T19:30:14.347+0000

In [0]:
%sql
Merge into dim_week w using vw_newweek_temp nw
on w.order_date = nw.order_date
when not matched then insert (order_date,last_updated_on) values(nw.order_date,nw.last_updated_on)

num_affected_rows num_updated_rows num_deleted_rows num_inserted_rows 64598 0 0 64598

In [0]:
%sql
select * from dim_week limit 5

week_id order_date week_of_month year quarter_number last_updated_on 1 2017-12-17T18:27:44.000+0000 3 2017 4 2023-12-19T19:25:31.742+0000 2 2017-12-23T02:20:41.000+0000 4 2017 4 2023-12-19T19:25:31.742+0000 3 2017-12-16T04:16:08.000+0000 3 2017 4 2023-12-19T19:25:31.742+0000 4 2017-11-29T18:24:23.000+0000 5 2017 4 2023-12-19T19:25:31.742+0000 5 2017-12-23T16:00:25.000+0000 4 2017 4 2023-12-19T19:25:31.742+0000


### Fact - Weekly Sales

In [0]:
%sql
create or replace temporary view vw_weekly_sales as
select distinct
  w.week_id,
  COALESCE(s.discount, 'No Discount') as discount,
  s.total_paid,
  s.quantity,
  CURRENT_TIMESTAMP() as last_updated_on
from
  silver_TcktSales_delta_part2 s
  left join dim_week w on s.order_date = w.order_date

In [0]:
%sql
select * from vw_weekly_sales limit 5

week_id discount total_paid quantity last_updated_on 61122 No Discount 20.94 1 2023-12-19T22:30:48.536+0000 40693 No Discount 20.94 1 2023-12-19T22:30:48.536+0000 11827 No Discount 35.0 1 2023-12-19T22:30:48.536+0000 31779 No Discount 22.0 1 2023-12-19T22:30:48.536+0000 40396 No Discount 22.0 1 2023-12-19T22:30:48.536+0000

In [0]:
%sql
merge into fact_weekly_sales f using vw_weekly_sales t
on f.week_id = t.week_id and f.discount = t.discount and f.total_paid = t.total_paid and f.quantity = t.quantity and f.last_updated_on = t.last_updated_on
when matched then 
  update set
    f.week_id = t.week_id,
    f.discount = t.discount,
    f.total_paid = t.total_paid,
    f.quantity = t.quantity,
    f.last_updated_on = t.last_updated_on
when not matched then 
  insert (
    week_id,
    discount,
    total_paid,
    quantity,
    last_updated_on
  ) values (
    t.week_id,
    t.discount,
    t.total_paid,
    t.quantity,
    t.last_updated_on
  );

num_affected_rows num_updated_rows num_deleted_rows num_inserted_rows 80402 0 0 80402

In [0]:
%sql
select * from fact_weekly_sales limit 5

weekly_sales_id week_id discount total_paid quantity last_updated_on 1 16 No Discount 42.99 1 2023-12-19T19:26:36.875+0000 2 18 No Discount 20.94 1 2023-12-19T19:26:36.875+0000 3 36 No Discount 22.0 1 2023-12-19T19:26:36.875+0000 4 31 No Discount 20.16 1 2023-12-19T19:26:36.875+0000 5 15 No Discount 42.99 1 2023-12-19T19:26:36.875+0000

At this stage, the data merging/updating aspect for the silver layer was complete.


### Gold Layer & Analysis


At this stage, the gold layer aggregation tables are created along with three forms of meaningful analysis & charts.

In developing three aggregated gold layer analysis tables that are derived from the fact and dimension tables, insights at the business-level can be successfully derived from the data.

### Analysis #1 - Ticket Sales by Affiliate

For my first gold level analysis, I wanted to create a table that analyzes the relation between affiliate and total sales. From a business standpoint, this analysis could prove beneficial in understanding which promoters are the best at contributing towards overall ticket sales.

In [0]:
%sql

drop table if exists analysis1_salesbyaffiliate

In [0]:
%sql
create or replace table analysis1_salesbyaffiliate (
  sales_by_affiliate_id BIGINT GENERATED BY DEFAULT AS IDENTITY (START WITH 1 INCREMENT BY 1),
  affiliate_id BIGINT,
  total_sales DOUBLE
)
using delta
LOCATION 'dbfs:/mnt/mount/fall_2023_finals/TicketSales/gold/analysis1'

In [0]:
%sql
insert into analysis1_salesbyaffiliate(affiliate_id,total_sales)
select
  COALESCE(af.affiliate_id, 3) as affiliate_id,
  ROUND(SUM(total_paid), 2) as total_sales
from
  fact_order_transaction f
  left join dim_affiliate af on f.affiliate_id = af.affiliate_id
group by
  COALESCE(af.affiliate_id, 3);

num_affected_rows num_inserted_rows 37 37

In [0]:
%sql
select * from analysis1_salesbyaffiliate limit 5

sales_by_affiliate_id affiliate_id total_sales 1 29 3394.02 2 26 2217.67 3 19 68.19 4 22 0.0 5 7 4010.99


At this point, I wanted to develop a Pie Chart that showed the total sales of the top 10 affiliates in proportion to one another.

In [0]:
%sql
select distinct affiliate_id, total_sales from analysis1_salesbyaffiliate order by total_sales desc limit 10

affiliate_id total_sales 4 1431791.17 3 817091.32 2 456120.5 34 11465.12 36 7164.54 7 4010.99 8 3437.03 29 3394.02 26 2217.67 1 2065.41

Databricks visualization. Run in Databricks to view.

In order to find out specifically which affiliates were among the top three highest contributors in the Pie Chart, I wrote the following query.

In [0]:
%sql
select distinct f.affiliate_id, a.affiliate as affiliate_name from
  fact_order_transaction f
  left join dim_affiliate a on f.affiliate_id = a.affiliate_id
where
  f.affiliate_id in (4, 3, 2)

affiliate_id affiliate_name 4 echckt 2 BoxOffice 3 No Affiliate


As a result of this query, the conclusion is that the best affiliates when it comes to making salse are echckt and BoxOffice. However, when it comes to direct rankings, the second highest sales were derived from tickets purchased through no affiliate at all. Thus making the cumulative ranking for total ticket sales as follows: 1. echckt 2. No Affiliate 3. BoxOffice


I also wanted to create a Bar Chart for this table to capture important data (affiliate_id 4, 3, and 2), so I wrote the following query to isolate the x-axis where affiliate_id is between 1 and 5.

In [0]:
%sql
select distinct affiliate_id, total_sales from analysis1_salesbyaffiliate where affiliate_id between 1 and 5;

affiliate_id total_sales 1 2065.41 4 1431791.17 3 817091.32 5 1599.37 2 456120.5

Databricks visualization. Run in Databricks to view.

With the Bar Chart, one can more easiliy see the top three affiliates that contributed most towards total sales, being affiliate_id 4, 3, and 2.

### Analysis #2 - Number of Orders/Sales by Order Location 

For my second gold level analysis, I wanted to create a table to analyze the numbers of total revenue and sales in relation to the order location. I figured this would be beneficial as it would allow a business to understand the specific locations where most of their sales are coming from and plan advertisements acccordingly.

In [0]:
%sql
drop table if exists analysis2_salesbylocation

In [0]:
%sql
create or replace table analysis2_salesbylocation (
  sales_by_location_id BIGINT GENERATED BY DEFAULT AS IDENTITY (START WITH 1 INCREMENT BY 1),
  order_location_id BIGINT,
  total_paid DOUBLE,
  total_sales INT
)
using delta
LOCATION 'dbfs:/mnt/mount/fall_2023_finals/TicketSales/gold/analysis2';


In [0]:
%sql
insert into analysis2_salesbylocation(order_location_id, total_paid, total_sales)
select
  order_location_id,
  ROUND(SUM(total_paid), 2) as total_paid,
  SUM(quantity) as total_sales
from
  fact_order_transaction
group by
  order_location_id;

num_affected_rows num_inserted_rows 538 538

In [0]:
%sql
select * from analysis2_salesbylocation limit 5

sales_by_location_id order_location_id total_paid total_sales 1 474 5286.09 280 2 29 3528.03 159 3 65 11292.04 523 4 418 3593.32 162 5 191 444.36 14

In [0]:
%sql
select distinct order_location_id, total_paid, total_sales from analysis2_salesbylocation where order_location_id between 1 and 20;

order_location_id total_paid total_sales 18 27420.22 1505 5 76720.95 4639 10 27673.03 1526 9 70150.85 3765 3 8697.95 433 14 16345.28 914 7 18728.02 858 6 220411.37 11358 15 14217.77 693 20 6825.38 355 2 3776.58 172 16 8113.08 471 4 469313.89 32719 1 554385.03 35073 8 18093.71 904 13 3642.69 159 17 14620.33 808 12 52458.2 2703 19 10739.4 564 11 57550.74 2939

Databricks visualization. Run in Databricks to view.

Databricks visualization. Run in Databricks to view.

Among the order_location_ids reflected on the Bar Chart, those with order_location_ids of 1, 4, and 6 for this sample greatly stood out to me as they were the top three earners both in terms of total paid and total sales. In order to find out exactly what those locations were, I wrote the following query.

In [0]:
%sql
select f.order_location_id, o.order_location, f.total_paid, f.total_sales from analysis2_salesbylocation f
join
  dim_order_location o on f.order_location_id = o.order_location_id
where
  f.order_location_id in (1, 4, 6);

order_location_id order_location total_paid total_sales 6 Los Angeles, CA, United States 220411.37 11358 1 Costa Mesa, CA, United States 554385.03 35073 4 Hacienda Heights, CA, United States 469313.89 32719



From this, we can conclude that among the snapshot of locations between 1 and 20, Costa Mesa was the order location that had the highest amount of total ticket sales along with revenue, followed by Hacienda Heights and Los Angeles, respectively.

### Analysis #3 - Sales Over Time Throughout a Given Time Period

For my third gold level analysis, I wanted to analyze how sales developed overtime leading up to the Christmas holiday. Since the dataset I analyzed was for Winter Fest OC, I assumed ticket sales leading up to the Winter/Christmas season holiday would be interesting to create a visual for in order to observe how sales developed.

In [0]:
%sql
drop table if exists analysis3_salesovertime

In [0]:
%sql
create or replace table analysis3_salesovertime (
  sales_over_time_id BIGINT GENERATED BY DEFAULT AS IDENTITY (START WITH 1 INCREMENT BY 1),
  date_id BIGINT,
  shortdate STRING,
  tickets_sold INT
)
using delta
LOCATION 'dbfs:/mnt/mount/fall_2023_finals/TicketSales/gold/analysis3';

In [0]:
%sql
insert into analysis3_salesovertime(date_id, shortdate, tickets_sold)
select distinct
  d.date_id,
  d.shortdate,
  SUM(f.quantity) over (order by d.date_id) as tickets_sold
from
  dim_date d
left join
  fact_order_transaction f on d.date_id = f.date_id
where
  d.shortdate is not NULL
order by
  d.date_id;

num_affected_rows num_inserted_rows 40 40

In [0]:
%sql
select * from analysis3_salesovertime limit 5

sales_over_time_id date_id shortdate tickets_sold 1 1 12-17-2017 2 2 2 12-19-2017 4 3 3 12-23-2017 7 4 4 12-03-2017 8 5 5 12-10-2017 9

In [0]:
%sql
select * from analysis3_salesovertime

sales_over_time_id date_id shortdate tickets_sold 1 1 12-17-2017 2 2 2 12-19-2017 4 3 3 12-23-2017 7 4 4 12-03-2017 8 5 5 12-10-2017 9 6 6 12-24-2017 13 7 7 12-18-2017 23 8 8 12-22-2017 30 9 9 12-20-2017 32 10 10 12-24-2017 34 11 11 11-28-2017 35 12 12 12-24-2017 40 13 13 12-21-2017 45 14 14 11-12-2017 49 15 15 12-24-2017 51 16 16 12-24-2017 54 17 17 12-24-2017 56 18 18 12-17-2017 58 19 19 12-21-2017 63 20 20 12-24-2017 65 21 21 12-16-2017 67 22 22 12-19-2017 73 23 23 12-23-2017 77 24 24 12-24-2017 79 25 25 12-17-2017 104 26 26 12-24-2017 106 27 27 12-23-2017 108 28 28 12-17-2017 109 29 29 12-23-2017 117 30 30 12-12-2017 118 31 31 12-24-2017 121 32 32 12-03-2017 122 33 33 11-29-2017 123 34 34 12-23-2017 125 35 35 12-24-2017 128 36 36 12-18-2017 130 37 37 12-11-2017 131 38 38 12-23-2017 135 39 39 12-23-2017 136 40 40 12-24-2017 138

Databricks visualization. Run in Databricks to view.


From the available shortdates where sales occurred, a line chart was developed for a time period that spanned over roughly one month from November 12th to December 24th. As we can see, the number of tickets sold from November 12th to December 12th is roughly the same. The major jump in ticket sales occurs on the dates leading up to Christmas, with the most sales occurring on December 23rd and December 24th, respectively. This seems to indicate that many individuals may choose to purchase tickets closer to Christmas or at the entrance of an event rather than ordering them ahead of time.


### UNIT Testing


Lastly, at this stage, some UNIT testing was performed on the silver and gold layer tables.

### UNIT Testing - Silver Layer Tables

Checking row counts.

In [0]:
%python

assert spark.table("silver_TcktSales_delta_part1").count() <= 100, "number of rows expected doesnt match"

In [0]:
%python

assert spark.table("silver_TcktSales_delta_part2").count() <= 159358, "number of rows expected doesnt match"

Just to be safe, in addition to my actual silver tables, I wanted to check my fact tables to ensure none of them exceeded the maximum possible number of rows from the combined part 1 and 2 silver tables.

In [0]:
%python

assert spark.table("fact_order_transaction").count() <= 159458, "number of rows expected doesnt match"

In [0]:
%python

assert spark.table("fact_weekly_sales").count() <= 159458, "number of rows expected doesnt match"

In [0]:
%python

assert spark.table("fact_monthly_sales").count() <= 159458, "number of rows expected doesnt match"

They all passed. Back to the testing the actual part 1 and part 2 silver tables.

Checking if table exists.

In [0]:
%python

assert spark.table("silver_TcktSales_delta_part1"), "Table silver_TcktSales_delta_part1 does not exists"

In [0]:
%python

assert spark.table("silver_TcktSales_delta_part2"), "Table silver_TcktSales_delta_part2 does not exists"

Checking for expected columns.

In [0]:
%python

assert spark.table("silver_TcktSales_delta_part1").columns == ['attendee_id', 'event_id', 'order_id', 'order_date', 'email', 'quantity', 'ticket_type', 'event_date', 'order_location',
 'order_city', 'order_state', 'order_country', 'discount', 'affiliate', 'total_paid', 'home_address_1', 'home_address_2', 'home_city', 'home_state', 'home_country', 'zip'], "columns missing or not in right order"

In [0]:
%python

assert spark.table("silver_TcktSales_delta_part2").columns == ['attendee_id', 'event_id', 'order_id', 'order_date', 'email', 'quantity', 'ticket_type', 'event_date', 'order_location',
 'order_city', 'order_state', 'order_country', 'discount', 'affiliate', 'total_paid', 'home_address_1', 'home_address_2', 'home_city', 'home_state', 'home_country', 'zip'], "columns missing or not in right order"

The silver tables passed each of the unit tests performed on them.

### UNIT Testing - Gold Layer Tables

Checking row counts.

In [0]:
%python

assert spark.table("analysis1_salesbyaffiliate").count() <= 159458, "number of rows expected doesnt match"

In [0]:
%python

assert spark.table("analysis2_salesbylocation").count() <= 159458, "number of rows expected doesnt match"

In [0]:
%python

assert spark.table("analysis3_salesovertime").count() <= 159458, "number of rows expected doesnt match"

Checking if tables exist.

In [0]:
%python

assert spark.table("analysis1_salesbyaffiliate"), "Table analysis1_salesbyaffiliate does not exists"

In [0]:
%python

assert spark.table("analysis2_salesbylocation"), "Table analysis2_salesbylocation does not exists"

In [0]:
%python

assert spark.table("analysis3_salesovertime"), "Table analysis3_salesovertime does not exists"

Checking for nulls.

In [0]:
%python

from pyspark.sql.functions import col

df = spark.table("analysis1_salesbyaffiliate")

for column in ["affiliate_id", "total_sales"]:
    null_count = df.filter(col(column).isNull()).count()
    assert null_count == 0, f"Column {column} contains {null_count} null values"

In [0]:
%python

from pyspark.sql.functions import col

df = spark.table("analysis2_salesbylocation")

for column in ["order_location_id", "total_sales", "total_quantity"]:
    null_count = df.filter(col(column).isNull()).count()
    assert null_count == 0, f"Column {column} contains {null_count} null values"

In [0]:
%python

from pyspark.sql.functions import col

df = spark.table("analysis3_salesovertime")

for column in ["date_id", "shortdate", "tickets_sold"]:
    null_count = df.filter(col(column).isNull()).count()
    assert null_count == 0, f"Column {column} contains {null_count} null values"

The gold tables passed each of the unit tests performed on them.